In [26]:
from valurap import path_planning
from valurap import gcode
import logging
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import IPython
import time
from IPython.display import display
import IPython


import imp
imp.reload(path_planning)
imp.reload(gcode)

logging.basicConfig(level=logging.DEBUG)
logging.getLogger('valurp.path_planning').setLevel(logging.DEBUG)

lines = gcode.reader("test.gcode")
pg = gcode.path_gen(lines)
sg = gcode.gen_segments(pg)
todo = []

for i, s in enumerate(sg):
    #print(str(s)[:100])
    if isinstance(s, gcode.do_move):
        print(i, s)
        if i != 4:
            assert s.deltas.get("X", 0) == 0
            assert s.deltas.get("Y", 0) == 0
    if isinstance(s, gcode.do_segment):
        print("segment", i, len(s.path))
        if i > 135:
            break
        elif i >= 10 and i <= 225:
            todo.append(s)

seg = np.array(todo[0].path)

Do Home
do_home
Set current ['E0']
Set current ['E0']
Set current ['E0']
Set current ['E0']
1 do_move(deltas={'Z': 2.5, 'F': 6000.0, 'line': 20})
2 do_move(deltas={'E': 3.0, 'F': 200.0, 'line': 23})
3 do_move(deltas={'E': -6.5, 'F': 1500.0, 'line': 27})
4 do_move(deltas={'X': -156.977, 'Y': 203.188, 'Z': -14.7, 'F': 3600.0, 'line': 31})
5 do_move(deltas={'E': 6.5, 'F': 1500.0, 'line': 33})
segment 6 264
7 do_move(deltas={'E': -6.5, 'F': 1500.0, 'line': 296})
segment 8 6
9 do_move(deltas={'E': 6.5, 'F': 1500.0, 'line': 303})
segment 10 917
11 do_move(deltas={'E': -6.5, 'F': 1500.0, 'line': 1221})
segment 12 11
13 do_move(deltas={'E': 6.5, 'F': 1500.0, 'line': 1232})
segment 14 942
15 do_move(deltas={'X': 0.0, 'Y': 0.0, 'Z': 0.3, 'F': 600.0, 'line': 2176})
segment 16 986
17 do_move(deltas={'E': -6.5, 'F': 1500.0, 'line': 3169})
segment 18 13
19 do_move(deltas={'E': 6.5, 'F': 1500.0, 'line': 3182})
segment 20 947
21 do_move(deltas={'X': 0.0, 'Y': 0.0, 'Z': 0.30000000000000004, 'F': 600.0,

In [27]:
######## All-in-One

t0 = time.time()
path, slowdowns = path_planning.make_path(seg)
corner_errors_slowdowns, cc = path_planning.process_corner_errors(path, slowdowns)
corner_space_slowdowns, cc = path_planning.process_corner_space(path, corner_errors_slowdowns)
plato_slowdowns = corner_space_slowdowns
for i in range(20):
    new_plato_slowdowns, stage_ok, cc, nc, sc = path_planning.process_plato(path, plato_slowdowns)
    plato_slowdowns = new_plato_slowdowns
    print("Result", i, len(sc[sc["slowdown"] < 0.999]))

    if stage_ok:
        break

final_slowdowns, stage_ok, cc1, nc1, sc1 = path_planning.process_plato(path, plato_slowdowns)
ce_slowdowns, ce1 = path_planning.process_corner_errors(path, plato_slowdowns)
cs_slowdowns, cs1 = path_planning.process_corner_space(path, plato_slowdowns)
speeds = path_planning.gen_speeds(path, plato_slowdowns)

assert stage_ok
t1 = time.time()
print("Planning time:", t1 - t0)


Result 0 807
Result 1 136
Result 2 50
Result 3 35
Result 4 16
Result 5 8
Result 6 8
Result 7 2
Result 8 0
Planning time: 13.79953145980835


In [4]:
all_segments["test_vx1"] = all_segments["vx0"] + all_segments["dt"] * all_segments["ax0"]
all_segments["test_vy1"] = all_segments["vy0"] + all_segments["dt"] * all_segments["ay0"]
all_segments["test_x1"] = all_segments["x0"] + all_segments["dt"] * all_segments["vx0"] + all_segments["dt"] * all_segments["dt"] * all_segments["ax0"]/2
all_segments["test_y1"] = all_segments["y0"] + all_segments["dt"] * all_segments["vy0"] + all_segments["dt"] * all_segments["dt"] * all_segments["ay0"]/2
print("bad vx1")
display(all_segments[abs(all_segments["test_vx1"] - all_segments["vx1"]) > 0.01])
print("bad vy1")
display(all_segments[abs(all_segments["test_vy1"] - all_segments["vy1"]) > 0.01])
print("bad x1")
display(all_segments[abs(all_segments["test_x1"] - all_segments["x1"]) > 0.0001])
print("bad y1")
display(all_segments[abs(all_segments["test_y1"] - all_segments["y1"]) > 0.0001])
print("ax non continuous")
display(all_segments[abs(all_segments["ax1"] - all_segments["ax0"]) > 0.001])
print("ay non continuous")
display(all_segments[abs(all_segments["ay1"] - all_segments["ay0"]) > 0.001])
print("vx non continuous")
display(all_segments[abs(all_segments["vx1"] - all_segments["vx0"].shift(-1)) > 0.001])
print("vy non continuous")
display(all_segments[abs(all_segments["vy1"] - all_segments["vy0"].shift(-1)) > 0.001])
print("x non continuous")
display(all_segments[abs(all_segments["x1"] - all_segments["x0"].shift(-1)) > 0.001])
print("y non continuous")
display(all_segments[abs(all_segments["y1"] - all_segments["y0"].shift(-1)) > 0.001])
print("src_part groups")
display(np.bincount(all_segments["src_idx"], weights=all_segments["src_part"]))
display(all_segments[np.isnan(all_segments["dt"])][["seg_type", "vx0", "vx1", "vy0", "vy1"]])


bad vx1


x0         y0        vx0        vy0         ax0         ay0  \
221    9.868000 -42.870000  -0.000072 -10.147490    0.000000  990.035530   
222    9.868020 -42.920998   0.199844  -1.597110  165.879612 -652.459806   
225    9.912234 -43.057979   6.950302  -9.267069 -734.267183  979.022911   
226    9.934462 -43.086512   5.767085  -5.455584 -814.422228  542.948152   
229    9.959876 -43.101063   7.111078  -1.862425 -204.457186   53.548311   
230   10.078003 -43.131979   1.573010  -0.202573  990.035472    0.000000   
239   51.050258 -43.092929   7.500091   5.550067 -391.522979 -289.727005   
240   51.087671 -43.064682   4.683205   4.849001 -674.825316 -981.564096   
241   51.098729 -43.048876   1.912954   4.190394  256.449802  986.943178   
1625  27.503000 -22.276000 -11.743972 -11.743717  989.927288  989.927288   
1626  27.432580 -22.346143  -2.216921  -1.612838 -126.683033  -77.839302   
1921  32.981000 -35.466000  11.737334  11.737334 -989.927700 -989.927700   
1922  33.051463 -35.395936   2.199648   1.371162  204.931172   97.522905   
2202  28.438000  -0.977000 -11.733430 -11.733430  989.927816  989.927816   
2203  28.367508  -1.046994  -2.191408  -1.187119 -282.676657 -104.309892   
2482  33.113000 -13.838000  11.738165  11.738165 -989.927675 -989.927675   
2483  33.183457 -13.767924   2.201606   1.405228  191.949671   95.119445   

             x1         y1        vx1        vy1  ...  src_idx  src_part  \
221    9.868020 -42.920998   0.199844  -1.597110  ...       74  1.000000   
222    9.892154 -43.016007   2.854243 -11.226690  ...       75  0.805148   
225    9.934462 -43.086512   5.767085  -5.455584  ...       76  0.604599   
226    9.945226 -43.094484   6.116337  -4.077558  ...       77  0.623653   
229   10.078003 -43.131979   1.573010  -0.202573  ...       78  0.937492   
230   10.129000 -43.132000  10.143807   0.000124  ...       79  1.000000   
239   51.087671 -43.064682   4.683205   4.849001  ...       82  0.754850   
240   51.098729 -43.048876   1.912954   4.190394  ...       83  1.000000   
241   51.124890 -42.949361   3.770713  14.511531  ...       84  0.784559   
1625  27.432580 -22.346143  -2.216921  -1.612838  ...      496  1.000000   
1626  26.193598 -23.107540 -17.975366 -11.044809  ...      497  0.844279   
1921  33.051463 -35.395936   2.199648   1.371162  ...      572  1.000000   
1922  33.885063 -34.999085  18.724297   8.910542  ...      573  0.773713   
2202  28.367508  -1.046994  -2.191408  -1.187119  ...      645  1.000000   
2203  27.726444  -1.283739 -19.262756  -7.108107  ...      646  0.715224   
2482  33.183457 -13.767924   2.201606   1.405228  ...      717  1.000000   
2483  34.063227 -13.331809  18.620665   9.227353  ...      718  0.784516   

          seg_type          t   src_de        de   test_vx1   test_vy1  \
221    short_plato   3.520897 -0.00255 -0.002550  -0.000072  -1.424192   
222    short_plato   3.535894 -0.00607 -0.004887   2.687550 -11.382086   
225    short_plato   3.543862 -0.00300 -0.001814   4.107230  -5.476306   
226    short_plato   3.545569 -0.00107 -0.000667   4.377301  -4.529061   
229    short_plato   3.575201 -0.00650 -0.006094   1.505505  -0.394299   
230    short_plato   3.584034 -0.00255 -0.002550  10.318397  -0.202573   
239    short_plato   4.122280 -0.00310 -0.002340   5.176687   3.830748   
240    short_plato   4.125640 -0.00097 -0.000970   2.416238   1.551594   
241    short_plato   4.136493 -0.00654 -0.005131   4.696366  14.902313   
1625   short_plato  43.954330  0.00000  0.000000  -0.392908  -0.392653   
1626  middle_plato  44.072404  0.00000  0.000000 -17.174863 -10.803618   
1921   short_plato  53.842486  0.00000  0.000000   0.285739   0.285739   
1922  middle_plato  53.919390  0.00000  0.000000  17.959602   8.871028   
2202   short_plato  67.531944  0.00000  0.000000  -0.217804  -0.217804   
2203   short_plato  67.589819  0.00000  0.000000 -18.551318  -7.224054   
2482   short_plato  80.210352  0.00000  0.000000   0.299707   0.299707   
2483  middle_plat

bad vy1


x0         y0        vx0        vy0         ax0         ay0  \
221    9.868000 -42.870000  -0.000072 -10.147490    0.000000  990.035530   
222    9.868020 -42.920998   0.199844  -1.597110  165.879612 -652.459806   
225    9.912234 -43.057979   6.950302  -9.267069 -734.267183  979.022911   
226    9.934462 -43.086512   5.767085  -5.455584 -814.422228  542.948152   
229    9.959876 -43.101063   7.111078  -1.862425 -204.457186   53.548311   
230   10.078003 -43.131979   1.573010  -0.202573  990.035472    0.000000   
239   51.050258 -43.092929   7.500091   5.550067 -391.522979 -289.727005   
240   51.087671 -43.064682   4.683205   4.849001 -674.825316 -981.564096   
241   51.098729 -43.048876   1.912954   4.190394  256.449802  986.943178   
1625  27.503000 -22.276000 -11.743972 -11.743717  989.927288  989.927288   
1626  27.432580 -22.346143  -2.216921  -1.612838 -126.683033  -77.839302   
1921  32.981000 -35.466000  11.737334  11.737334 -989.927700 -989.927700   
1922  33.051463 -35.395936   2.199648   1.371162  204.931172   97.522905   
2202  28.438000  -0.977000 -11.733430 -11.733430  989.927816  989.927816   
2203  28.367508  -1.046994  -2.191408  -1.187119 -282.676657 -104.309892   
2482  33.113000 -13.838000  11.738165  11.738165 -989.927675 -989.927675   
2483  33.183457 -13.767924   2.201606   1.405228  191.949671   95.119445   

             x1         y1        vx1        vy1  ...  src_idx  src_part  \
221    9.868020 -42.920998   0.199844  -1.597110  ...       74  1.000000   
222    9.892154 -43.016007   2.854243 -11.226690  ...       75  0.805148   
225    9.934462 -43.086512   5.767085  -5.455584  ...       76  0.604599   
226    9.945226 -43.094484   6.116337  -4.077558  ...       77  0.623653   
229   10.078003 -43.131979   1.573010  -0.202573  ...       78  0.937492   
230   10.129000 -43.132000  10.143807   0.000124  ...       79  1.000000   
239   51.087671 -43.064682   4.683205   4.849001  ...       82  0.754850   
240   51.098729 -43.048876   1.912954   4.190394  ...       83  1.000000   
241   51.124890 -42.949361   3.770713  14.511531  ...       84  0.784559   
1625  27.432580 -22.346143  -2.216921  -1.612838  ...      496  1.000000   
1626  26.193598 -23.107540 -17.975366 -11.044809  ...      497  0.844279   
1921  33.051463 -35.395936   2.199648   1.371162  ...      572  1.000000   
1922  33.885063 -34.999085  18.724297   8.910542  ...      573  0.773713   
2202  28.367508  -1.046994  -2.191408  -1.187119  ...      645  1.000000   
2203  27.726444  -1.283739 -19.262756  -7.108107  ...      646  0.715224   
2482  33.183457 -13.767924   2.201606   1.405228  ...      717  1.000000   
2483  34.063227 -13.331809  18.620665   9.227353  ...      718  0.784516   

          seg_type          t   src_de        de   test_vx1   test_vy1  \
221    short_plato   3.520897 -0.00255 -0.002550  -0.000072  -1.424192   
222    short_plato   3.535894 -0.00607 -0.004887   2.687550 -11.382086   
225    short_plato   3.543862 -0.00300 -0.001814   4.107230  -5.476306   
226    short_plato   3.545569 -0.00107 -0.000667   4.377301  -4.529061   
229    short_plato   3.575201 -0.00650 -0.006094   1.505505  -0.394299   
230    short_plato   3.584034 -0.00255 -0.002550  10.318397  -0.202573   
239    short_plato   4.122280 -0.00310 -0.002340   5.176687   3.830748   
240    short_plato   4.125640 -0.00097 -0.000970   2.416238   1.551594   
241    short_plato   4.136493 -0.00654 -0.005131   4.696366  14.902313   
1625   short_plato  43.954330  0.00000  0.000000  -0.392908  -0.392653   
1626  middle_plato  44.072404  0.00000  0.000000 -17.174863 -10.803618   
1921   short_plato  53.842486  0.00000  0.000000   0.285739   0.285739   
1922  middle_plato  53.919390  0.00000  0.000000  17.959602   8.871028   
2202   short_plato  67.531944  0.00000  0.000000  -0.217804  -0.217804   
2203   short_plato  67.589819  0.00000  0.000000 -18.551318  -7.224054   
2482   short_plato  80.210352  0.00000  0.000000   0.299707   0.299707   
2483  middle_plat

bad x1


...

y non continuous


Empty DataFrame
Columns: [x0, y0, vx0, vy0, ax0, ay0, x1, y1, vx1, vy1, ax1, ay1, dt, src_idx, src_part, seg_type, t, src_de, de, test_vx1, test_vy1, test_x1, test_y1]
Index: []

[0 rows x 23 columns]

src_part groups


array([0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1.

Empty DataFrame
Columns: [seg_type, vx0, vx1, vy0, vy1]
Index: []

In [28]:
all_segments = path_planning.build_segments(path, plato_slowdowns)
acc_step = 10000
pr_opt = path_planning.format_segments(all_segments, acc_step=acc_step)


<ApgState x=8771010413199.0 v=0 a=0 j=0 jj=0> <ApgState x=-8387212135628.0 v=0 a=0 j=0 jj=0>
index: 0 start
x: 25.527 25.527
y: -24.41 -24.41
vx: 0.0 0.0
vy: 0.0 0.0
dx: 0.24518947197976715
dy: 0.2199463364679275
dvx: 22.144501438495595
dvy: 19.864645594194783
int_dt: 221.0
int_dx: 84246461078.12866 int_dy: 75572985760.38086
int_vx0: 0.0 int_vy0: 0.0
int_vx1: 152176.0 int_vy1: 136509.0
int_ax: 45154304.0 0.0105133056640625 int_ay1: 40501248.0 0.009429931640625
x_error to big 0.0014508581898660111
x_error: 0.0014508581898660111
x_error: 0.0014508581898660111 int_jx: -7264 int_ax: 45956976
y_error to big 0.0013244738813398271
y_error: 0.0013244738813398271
y_error: 0.0013244738813398271 int_jy: -6631 int_ay: 41233974
ApgStates: 25.77203657186765 -24.190213431220037
        V: 22.143794922158122 19.860308384522796
   max_xv: 22.045423975214362 0.0
   max_yv: 19.772123778238893 0.0
final x_error: -0.0001529001121198803
final y_error: -0.00015976768796477359
final vx_error: -0.0007065163374

ApgStates: 29.66164353186905 -22.237904109724333
        V: 67.40214303135872 8.66726622916758
   max_xv: 67.38919182680547 66.3401442579925
   max_yv: 16.853009583428502 8.767092367634177
final x_error: 0.00033015031664263006
final y_error: 0.0006495545344655795
final vx_error: -0.0044082655956572125
final vy_error: 0.002037518734869792
index: 9 start
x: 29.66164353186905 29.661313381552407
y: -22.237904109724333 -22.2385536642588
vx: 67.40214303135872 67.40655129695438
vy: 8.66726622916758 8.66522871043271
dx: 0.5561713821895893
dy: 0.03678152270651225
dvx: 1.0574919812579537
dvy: -8.19394379979063
int_dt: 82.0
int_dx: 191099031798.03223 int_dy: 12638034969.724121
int_vx0: 463184.0 int_vy0: 59561.0
int_vx1: 470451.0 int_vy1: 3253.0
int_ax: 5832704.0 0.0013580322265625 int_ay1: -45023232.0 -0.0104827880859375
x_error: -0.0008272856996853761 int_jx: 0 int_ax: 5832704.0
y_error to big -0.0010894728774317741
y_error: -0.0010894728774317741
y_error: -0.0010894728774317741 int_jy: 106786 i

index: 19 short_plato
x: 34.64678748626902 34.646812193875924
y: -23.673169636831155 -23.673497962328515
vx: 57.71362339146435 57.719011099142236
vy: -50.31033651903272 -50.31173800808549
dx: 0.3221032518550899
dy: -0.28107345656702876
dvx: 2.864593408891878
dvy: -2.4936757919443053
int_dt: 54.0
int_dx: 110673834612.229 int_dy: -96576104298.3252
int_vx0: 396605.0 int_vy0: -345730.0
int_vx1: 416290.0 int_vy1: -362866.0
int_ax: 23920640.0 0.0055694580078125 int_ay1: -20774912.0 -0.0048370361328125
x_error to big 0.0028490019386779863
x_error: 0.0028490019386779863
x_error: 0.0028490019386779863 int_jx: -977806 int_ax: 50321402
y_error to big -0.0027964977149537162
y_error: -0.0027964977149537162
y_error: -0.0027964977149537162 int_jy: 959786 int_ay: -46689134
ApgStates: 34.969035225218974 -23.954404752666598
        V: 60.63652108423412 -52.86274245008826
   max_xv: 60.6411776971072 57.71362339146435
   max_yv: -50.31033651903272 -52.887480705976486
final x_error: 0.0001444870948645871
f

dx: 0.1016584926835904
dy: -0.5357059658505108
dvx: -8.029119908506276
dvy: -2.0249481485648175
int_dt: 80.0
int_dx: 34929592114.93408 int_dy: -184067168288.00293
int_vx0: 114777.0 int_vy0: -451683.0
int_vx1: 59601.0 int_vy1: -465598.0
int_ax: -45219840.0 -0.010528564453125 int_ay1: -11403264.0 -0.002655029296875
x_error: -0.0002305252857794926 int_jx: 0 int_ax: -45219840.0
y_error to big -0.0018765226937915713
y_error: -0.0018765226937915713
y_error: -0.0018765226937915713 int_jy: 198073 int_ay: -19326184
ApgStates: 36.96586410863965 -27.667058720916977
        V: 8.66959453560412 -67.7774369250983
   max_xv: 16.70225174166262 8.77000275067985
   max_yv: -65.72852726094425 -67.76914233341813
final x_error: 0.0002305252857794926
final y_error: -8.944105356079035e-05
final vx_error: -0.003537297552226093
final vy_error: -0.023961515589235205
index: 28 short_plato
x: 36.96586410863965 36.96563358335387
y: -27.667058720916977 -27.666969279863416
vx: 8.66959453560412 8.673131833156345
vy: 

final y_error: -8.298352165070355e-05
final vx_error: -0.02211343540692212
final vy_error: -0.021176449367558803
index: 37 short_plato
x: 36.03475556359335 36.03441804130796
y: -32.26210139292525 -32.2620184094036
vx: -41.8313720729202 -41.80925863751328
vy: -61.68163963593543 -61.660463186567874
dx: -0.2280441626387244
dy: -0.33573968763774786
dvx: -3.3883108022683572
dvy: -5.008530964986697
int_dt: 52.0
int_dx: -78355377646.16211 int_dy: -115359278269.8706
int_vx0: -287463.0 int_vy0: -423873.0
int_vx1: -310747.0 int_vy1: -458291.0
int_ax: -29360128.0 -0.0068359375 int_ay1: -43384832.0 -0.010101318359375
x_error to big -0.0018764917219584731
x_error: -0.0018764917219584731
x_error: -0.0018764917219584731 int_jx: 721236 int_ax: -48112264
y_error to big -0.0022213157204404865
y_error: -0.0022213157204404865
max_ay violation, slow down -763238269.8706055 65582878.0 54043195.52844595
y_error: -0.0017770525763523893
max_ay violation, slow down -610590615.8964844 61143274.0 54043195.5284459

...

int_dx: 693037007499.5642 int_dy: 693188044132.6587
int_vx0: 436093.0 int_vy0: 435953.0
int_vx1: 41950.0 int_vy1: 41950.0
int_ax: -44892160.0 -0.0104522705078125 int_ay1: -44892160.0 -0.0104522705078125
x_error to big 0.013039265466982641
x_error: 0.013039265466982641
x_error: 0.013039265466982641 int_jx: -3707 int_ax: -43826398
y_error to big 0.014650269099099944
y_error: 0.014650269099099944
y_error: 0.014650269099099944 int_jy: -4165 int_ay: -43694722
ApgStates: 26.071989699846018 47.00300146759255
        V: 6.104091880843043 6.084010237827896
   max_xv: 63.45988367684186 6.206246325746178
   max_yv: 63.43951099552215 6.1864557210356
final x_error: -0.001128479196818688
final y_error: -0.0011167114503294329
final vx_error: -0.00036466193301443184
final vy_error: -0.020446304948160687
index: 3186 end
x: 26.071989699846018 26.073118179042837
y: 47.00300146759255 47.00411817904288
vx: 6.104091880843043 6.104456542776058
vy: 6.084010237827896 6.104456542776057
dx: 0.005485694198032576


y_error to big 0.012986073116337593
y_error: 0.012986073116337593
y_error: 0.012986073116337593 int_jy: -5020 int_ay: 46456994
ApgStates: 11.10611170064367 32.60208852406358
        V: -11.754018487408757 -11.760421330109239
   max_xv: -11.850788723677397 -63.831685110926635
   max_yv: -11.857773642987013 -63.761835917830474
final x_error: -0.0008882993563119612
final y_error: -0.0009114759364479141
final vx_error: -0.05374309199004834
final vy_error: -0.06014593469038232
index: 3194 short_plato
x: 11.10611170064367 11.106999999999982
y: 32.60208852406358 32.60300000000003
vx: -11.754018487408757 -11.700275395418709
vy: -11.760421330109239 -11.700275395418856
dx: -0.06792864495195694
dy: -0.06790546837182632
dvx: 10.948602864288485
dvy: 10.955005706988945
int_dt: 110.0
int_dx: -23340104682.420044 int_dy: -23332141270.12451
int_vx0: -80773.0 int_vy0: -80817.0
int_vx1: -5535.0 int_vy1: -5535.0
int_ax: 44826624.0 0.01043701171875 int_ay1: 44826624.0 0.01043701171875
x_error to big 0.00169

x_error: 0.0017493735277369638 int_jx: -89089 int_ax: 49501235
y_error: 0.0005600368022911084 int_jy: 0 int_ay: -720896.0
ApgStates: 23.641738511502627 46.26817547067767
        V: -12.303353287279604 -12.306409189477563
   max_xv: -12.393284123390913 -22.48838427476585
   max_yv: -12.143136700615289 -12.30480847880244
final x_error: 1.3358171536026475e-05
final y_error: -0.0005600368022911084
final vx_error: -0.00020494140989057996
final vy_error: -0.0042777167664471705
index: 3209 long_plato_in
x: 23.641738511502627 23.64172515333109
y: 46.26817547067767 46.26873550747996
vx: -12.303353287279604 -12.303148345869714
vy: -12.306409189477563 -12.302131472711116
dx: -1.9494970046820193
dy: -1.9487624820409053
dvx: -51.33888702716441
dvy: -51.33057100096327
int_dt: 513.0
int_dx: -669842070300.7385 int_dy: -669589690242.998
int_vx0: -84548.0 int_vy0: -84569.0
int_vx1: -437346.0 int_vy1: -437310.0
int_ax: -45088768.0 -0.010498046875 int_ay1: -45088768.0 -0.010498046875
x_error to big -0.003

y_error: 0.004704039659920056 int_jy: -1916 int_ay: 45511812
ApgStates: 14.032744448047016 37.225745907553936
        V: 63.64047294482589 63.574552768841386
   max_xv: 63.54122888296842 12.61694706045091
   max_yv: 63.47574526444077 12.624950613826512
final x_error: -0.0009103596752346732
final y_error: -0.0009089001683619813
final vx_error: 0.0008626380365939212
final vy_error: -0.0650575379478795
index: 3219 long_plato_main
x: 14.032744448047016 14.03365480772225
y: 37.225745907553936 37.2266548077223
vx: 63.64047294482589 63.639610306789294
vy: 63.574552768841386 63.639610306789265
dx: 6.8587141178178825
dy: 6.858712658311006
dvx: -0.0008626380365939212
dvy: 0.0650575379478795
int_dt: 1078.0
int_dx: 2356636226291.3037 int_dy: 2356635724808.5596
int_vx0: 437334.0 int_vy0: 436881.0
int_vx1: 437328.0 int_vy1: 437328.0
int_ax: -0.0 -0.0 int_ay1: 0.0 0.0
x_error to big -0.0017288656343481534
x_error: -0.0017288656343481534
x_error: -0.0017288656343481534 int_jx: 75 int_ax: -40425
y_erro

x: 12.43044636270206 12.430550605640793
y: 36.19077436268562 36.19096594035337
vx: 1.0762596502900124 1.0765475011334256
vy: 2.058804966509342 2.059179711376371
dx: 0.39107630863595944
dy: 0.7480282913761798
dvx: 18.773398124260925
dvy: 35.90887646332631
int_dt: 374.0
int_dx: 134372796466.54785 int_dy: 257020563835.47607
int_vx0: 7396.0 int_vy0: 14148.0
int_vx1: 136406.0 int_vy1: 260912.0
int_ax: 22609920.0 0.0052642822265625 int_ay1: 43253760.0 0.01007080078125
x_error: 0.0006455272277463564 int_jx: 0 int_ax: 22609920.0
y_error to big 0.0011219638268116228
y_error: 0.0011219638268116228
y_error: 0.0011219638268116228 int_jy: -1159 int_ay: 43470493
ApgStates: 12.820877144110273 36.938313058263155
        V: 19.85259586945176 37.95212251134217
   max_xv: 19.802391761913896 1.0762596502900124
   max_yv: 37.85666194744408 2.058804966509342
final x_error: -0.0006455272277463564
final y_error: -0.0004895957986477129
final vx_error: 0.002938094900823529
final vy_error: -0.015558918493482565


In [18]:
import valurap.commands as vac
import valurap.printer as vp
import valurap.axes as vax
import valurap.apgs as vap
import valurap.path_planning as vapp

from importlib import reload
reload(vac)
reload(vax)
reload(vap)
reload(vp)
reload(vapp)

prn = vp.Valurap()
prn.setup()

DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


Executing reset code


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


Update axes
Reset OLED
Setup done


In [5]:
prn.home()

DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


SetPositions: {'Z': 0}


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


Move: {'Z': 30000}


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngI

...

DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngI

Save position: Z 19997.6796875
SetPositions: {'X1': 0, 'X2': 0, 'Y': 0}


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


SetPositions: {'X1': 13200, 'X2': -14000, 'Y': -22500}
MoveTo: {'X1': 12700, 'X2': -13500, 'Y': -20000}
Move: {'X1': -500.0, 'X2': 500.0, 'Y': 2500.0}


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


In [6]:
prn.move(Z=15000)

Move: {'Z': 15000}
Save position: X1 12698.84765625
Save position: X2 -13501.1484375
Save position: Y -20001.1484375


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


SetPositions: {'X2': -13501.1484375, 'Y': -20001.1484375, 'Z': 19997.6796875}


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


In [7]:
prn.moveto(X1=0)
prn.moveto(Y=0)


MoveTo: {'X1': 0}
Save position: X2 -13502.1484375
Save position: Y -20002.1484375
Save position: Z 34996.359375
SetPositions: {'X1': 12698.84765625, 'Y': -20002.1484375, 'Z': 34996.359375}


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


Move: {'X1': -12697.84765625}
Save position: X1 12697.84765625
Save position: Y -20003.1484375


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


MoveTo: {'Y': 0}
Save position: X1 -0.4140625
Move: {'Y': 20003.1484375}


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216
DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


In [30]:
import valurap.asg as vas
imp.reload(vas)

for axe in prn.axes.values():
    axe.apg = None
    axe.enabled = False
 
prn.axe_x1.apg = prn.apg_x
prn.axe_y.apg = prn.apg_y
prn.axe_e1.apg = prn.apg_z
prn.axe_y.enabled = True
prn.axe_x1.enabled = True
prn.axe_e1.enabled = False
prn.update_axes_config()

path_code = prn.asg.gen_path_code(pr_opt, accel_step=int(50000000/acc_step), real_apgs={"X": prn.apg_x, "Y": prn.apg_y, "Z": prn.apg_z})
print(len(path_code))

try:
    prn.exec_long_code(path_code, splits=2000, verbose=True)
except:
    prn.setup()

DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


SetPositions: {'X1': 0, 'Y': 0, 'E1': 0}
24233


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


sent 2000 commands to addr 0, left 22233
Busy: 1 Wait: 1 Error: 2 PC: 31 Cur addr: 2000 Cur len: 22233
free_buf: 6223


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


...

Busy: 1 Wait: 1 Error: 2 PC: 24153 Cur addr: 7849 Cur len: 0


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


Busy: 1 Wait: 1 Error: 2 PC: 24210 Cur addr: 7849 Cur len: 0


DEBUG:PIL.PngImagePlugin:STREAM b'IHDR' 16 13
DEBUG:PIL.PngImagePlugin:STREAM b'IDAT' 41 1216


Busy: 0 Wait: 0 Error: 0 PC: 24232 Cur addr: 7849 Cur len: 0


In [ ]:
res = path_planning.emulate(pr_opt, accel_step=50000000/acc_step, verbose=0)
spm = 80
res["x"] = res["X_x"] / spm
res["y"] = res["Y_x"] / spm
res["xv"] = res["X_v"] * 65536 / 2**32 / spm * 50000000
res["yv"] = res["Y_v"] * 65536 / 2**32 / spm * 50000000
res[["x", "y", "xv", "yv", "ts"]]

In [ ]:
%matplotlib notebook

from matplotlib.collections import LineCollection
import warnings

warnings.simplefilter("error")

lines = []
colors = []

i = 0
for index, row in all_segments.iterrows():
    i += 1
    lines.append(((row['x0'], row['y0']), (row['x1'], row['y1'])))
    st = row["seg_type"]
    if st == "start":
        colors.append((1,0,0,1))
    elif st == "end":
        colors.append((0,1,0,1))
    elif st == "short_plato":
        colors.append((0,0.3,1,1))
    elif st == "middle_plato":
        colors.append((0.8,0,0.8,1))
    elif st == "long_plato_main":
        colors.append((0.2,0.2,0.2,1))
    elif st == "long_plato_in":
        colors.append((1,0,0.8,1))
    elif st == "long_plato_out":
        colors.append((0,1,0.8,1))
    else:
        colors.append((1,1,0,1))
    
lc = LineCollection(lines, colors=colors, linewidths=1)
fig, ax = plt.subplots()

ax.add_collection(lc)

#path.iloc[limit:].plot(x="px", y="py", linewidth=3, color=(0.5, 0.5, 0.5, 0.2), ax=ax)
full_path = pd.DataFrame()
full_path["x"] = path["px"]
full_path["y"] = path["py"]
last_x = path["x"].iloc[-1]
last_y = path["y"].iloc[-1]
full_path = full_path.append({"x": last_x, "y": last_y}, ignore_index=True)
full_path.plot(x="x", y="y", linewidth=5, color=(0.5, 0.5, 0.5, 0.2), ax=ax)
    
ax.autoscale()
ax.margins(0.1)


In [ ]:
all_segments["test_vx1"] = all_segments["vx0"] + all_segments["dt"] * all_segments["ax0"]
all_segments["test_vy1"] = all_segments["vy0"] + all_segments["dt"] * all_segments["ay0"]
all_segments["test_x1"] = all_segments["x0"] + all_segments["dt"] * all_segments["vx0"] + all_segments["dt"] * all_segments["dt"] * all_segments["ax0"]/2
all_segments["test_y1"] = all_segments["y0"] + all_segments["dt"] * all_segments["vy0"] + all_segments["dt"] * all_segments["dt"] * all_segments["ay0"]/2
print("bad vx1")
display(all_segments[abs(all_segments["test_vx1"] - all_segments["vx1"]) > 0.01])
print("bad vy1")
display(all_segments[abs(all_segments["test_vy1"] - all_segments["vy1"]) > 0.01])
print("bad x1")
display(all_segments[abs(all_segments["test_x1"] - all_segments["x1"]) > 0.0001])
print("bad y1")
display(all_segments[abs(all_segments["test_y1"] - all_segments["y1"]) > 0.0001])
print("ax non continuous")
display(all_segments[abs(all_segments["ax1"] - all_segments["ax0"]) > 0.001])
print("ay non continuous")
display(all_segments[abs(all_segments["ay1"] - all_segments["ay0"]) > 0.001])
print("vx non continuous")
display(all_segments[abs(all_segments["vx1"] - all_segments["vx0"].shift(-1)) > 0.001])
print("vy non continuous")
display(all_segments[abs(all_segments["vy1"] - all_segments["vy0"].shift(-1)) > 0.001])
print("x non continuous")
display(all_segments[abs(all_segments["x1"] - all_segments["x0"].shift(-1)) > 0.001])
print("y non continuous")
display(all_segments[abs(all_segments["y1"] - all_segments["y0"].shift(-1)) > 0.001])
print("src_part groups")
display(np.bincount(all_segments["src_idx"], weights=all_segments["src_part"]))
display(all_segments[np.isnan(all_segments["dt"])][["seg_type", "vx0", "vx1", "vy0", "vy1"]])
